# Dependencies

In [1]:
import polars as pl
import numpy as np
import yfinance as yf
import warnings

warnings.filterwarnings("ignore")

import plotly.graph_objects as go
import plotly.express as px

import pandas as pd
from ripser import Rips
import persim
from ordpy import weighted_permutation_entropy

from hedging_strategy import hedging_strategies, portfolio, risk

# Market Crash Indicators

In [2]:
# Define index names and date range
index_names = ["^GSPC", "^DJI", "^IXIC", "^RUT"]
start_date_string = "1997-01-01"
# start_date_string = '2021-01-01'
end_date_string = "2024-04-21"

# Download and prepare data
raw_data = yf.download(index_names, start=start_date_string, end=end_date_string)
df_close = raw_data["Adj Close"].dropna(axis="rows")
df_close.index = pd.to_datetime(raw_data.index.strftime("%Y-%m-%d"))
P = df_close.to_numpy()
r = np.log(np.divide(P[1:], P[:-1]))

# Handle NaN values that might appear after log return calculation
r = np.nan_to_num(r)  # Replace NaNs with zero (or you might choose to drop them)


# Define and compute Wasserstein distances and permutation entropy
rips = Rips(maxdim=2)
w = 20
n = len(raw_data) - (2 * w) + 1
wasserstein_dists = np.zeros((n, 1))
perm_entropy = np.zeros(n)
hawkes_values = np.zeros(n)


# Define the Hawkes process function
def hawkes_process(data, decay):
    alpha = np.exp(-decay)
    output = np.zeros_like(data)
    output[0] = data[0]
    for t in range(1, len(data)):
        output[t] = alpha * output[t - 1] + (1 - alpha) * data[t]
    return output


for i in range(n):
    dgm1 = rips.fit_transform(r[i : i + w])
    dgm2 = rips.fit_transform(r[i + w + 1 : i + (2 * w) + 1])
    wasserstein_dists[i] = persim.wasserstein(dgm1[0], dgm2[0])
    # # Calculate permutation entropy for the window
    # perm_entropy[i] = permutation_entropy(r[i:i+(2*w)+1], dx=1, dy=1, taux=1, tauy=1, normalized=True)
    # Calculate permutation entropy for the window, ensuring data is appropriately shaped
    flat_data = r[i : i + (2 * w) + 1].flatten()  # Flatten the data
    perm_entropy[i] = weighted_permutation_entropy(flat_data, dx=10, normalized=True)
    hawkes_values[i] = hawkes_process(flat_data, decay=0.1)[-1]


df_close["Wasserstein_distances"] = np.concatenate(
    (np.zeros(len(df_close) - len(wasserstein_dists)), wasserstein_dists.flatten())
)

df_close["Permutation_Entropy"] = np.concatenate(
    (np.zeros(len(df_close) - len(perm_entropy)), perm_entropy)
)

df_close["Hawkes_Process"] = np.concatenate(
    (np.zeros(len(df_close) - len(hawkes_values)), hawkes_values)
)

df_close.reset_index(inplace=True)
df_close.to_csv("Data/prices_with_indicators.csv", index=False)

[*********************100%***********************]  4 of 4 completed


Rips(maxdim=2, thresh=inf, coeff=2, do_cocycles=False, n_perm = None, verbose=True)


In [3]:
df = pd.read_csv("Data/prices_with_indicators.csv")

## Visualize indicators 

In [4]:
fig = go.Figure()

fig.add_trace(
    go.Scatter(x=df["Date"], y=df["^GSPC"], name="^GSPC", yaxis="y1", mode="lines")
)

indicators = ["Wasserstein_distances", "Permutation_Entropy", "Hawkes_Process"]
for col in indicators:

    fig.add_trace(
        go.Scatter(x=df["Date"], y=df[col], name=col, yaxis="y2", mode="lines")
    )


fig.update_layout(
    title="Homology, Permutation Entropy, and Market Drawdowns with Peaks",
    xaxis=dict(title="Date"),
    yaxis=dict(title="^GSPC", side="left", showgrid=True),
    yaxis2=dict(title="indicators", side="right", overlaying="y", showgrid=False),
)

# Define Hedging indicator

In [5]:
read_hedge_010 = pd.read_csv("./arima_vix/arima111.csv")
hedge = pd.Series(read_hedge_010["hedge_signal"])
hedge

0       0.0
1       0.0
2       0.0
3       0.0
4       0.0
       ... 
6865    0.0
6866    0.0
6867    0.0
6868    0.0
6869    0.0
Name: hedge_signal, Length: 6870, dtype: float64

In [6]:
df['hedge'] = hedge

# np.where(
#     (df['Wasserstein_distances'] > 0.17) & (df['Wasserstein_distances'].shift() < 0.17),
#     1,
#     0,
# )

# check if hedge implemented in the past 300 days
hedge = df['hedge'].values
for i in range(300, len(hedge)):
    if any(hedge[i - 300 : i]):
        hedge[i] = 0
    else:
        hedge[i]

hedge = df['hedge'].values
for i in range(300, len(hedge)):
    if any(hedge[i - 300 : i]):
        hedge[i] = 0
    else:
        hedge[i]

hedge[: 300] = 0
df['hedge'] = hedge

hedge_events = df[df['hedge'] == 1][['Date', '^GSPC']].to_dict(orient='records')

In [7]:
df

Date          ^DJI        ^GSPC         ^IXIC         ^RUT  \
0     1997-01-02   6442.490234   737.010010   1280.699951   358.959991   
1     1997-01-03   6544.089844   748.030029   1310.680054   361.850006   
2     1997-01-06   6567.180176   747.650024   1316.400024   362.309998   
3     1997-01-07   6600.660156   753.229980   1327.729980   364.160004   
4     1997-01-08   6549.479980   748.409973   1320.349976   364.170013   
...          ...           ...          ...           ...          ...   
6865  2024-04-15  37735.109375  5061.819824  15885.019531  1975.709961   
6866  2024-04-16  37798.968750  5051.410156  15865.250000  1967.479980   
6867  2024-04-17  37753.308594  5022.209961  15683.370117  1947.949951   
6868  2024-04-18  37775.378906  5011.120117  15601.500000  1942.959961   
6869  2024-04-19  37986.398438  4967.229980  15282.009766  1947.660034   

      Wasserstein_distances  Permutation_Entropy  Hawkes_Process  hedge  
0                  0.000000             0.000000        0.000000    0.0  
1                  0.000000             0.000000        0.000000    0.0  
2                  0.000000             0.000000        0.000000    0.0  
3                  0.000000             0.000000        0.000000    0.0  
4                  0.000000             0.000000        0.000000    0.0  
...                     ...                  ...             ...    ...  
6865               0.025275             0.322148       -0.006382    0.0  
6866               0.027154             0.323017       -0.005104    0.0  
6867               0.023793             0.323209       -0.005266    0.0  
6868               0.033141             0.321668       -0.005266    0.0  
6869               0.037522             0.320473       -0.005266    0.0  

[6870 rows x 9 columns]

# Portfolio Holding & Reading Options Data

In [8]:
spy = yf.download("SPY")[["Adj Close"]] * 500  # assume we hold 500 shares
spy_pl = (
    pl.from_pandas(spy.reset_index())
    .with_columns(pl.col("Date").cast(pl.Date))
    .rename({"Adj Close": "Holding"})
)

[*********************100%***********************]  1 of 1 completed


In [9]:
option_data = pl.read_parquet("Data/SPX_options_1996_2024.parquet").with_columns(
    pl.col("date").cast(pl.Date), pl.col("exdate").cast(pl.Date)
)

# Excecute Hedging

In [10]:
all_var = pl.DataFrame()

for event in hedge_events:
    hedge_date = event["Date"]

    hedge = hedging_strategies.hedging(
        hedge_date=hedge_date,
        holding_period=300,
        options=option_data,
        min_dte=300,
        close=event["^GSPC"],
    )

    long_put_value = hedge.buy_put()
    short_call_value = hedge.short_call()
    bear_put_spread_value = hedge.bear_put_spread(
        strike2=(
            spy_pl.filter(
                pl.col("Date").is_between(
                    pl.lit(hedge_date).str.strptime(pl.Date, "%Y-%m-%d")
                    - pl.duration(days=60),
                    pl.lit(hedge_date).str.strptime(pl.Date, "%Y-%m-%d"),
                )
            )["Holding"].min()
            / 50
        )
    )

    port = portfolio.portfolio(hedge_date=hedge_date, holding_value=spy_pl)

    do_nothing = port.compute_portfolio()

    long_put = port.compute_portfolio(
        hedge_value=(long_put_value.select("date", "hedge_value"))
    )

    short_call = port.compute_portfolio(
        hedge_value=(short_call_value.select("date", "hedge_value"))
    )

    bear_put_spread = port.compute_portfolio(
        hedge_value=(bear_put_spread_value.select("date", "hedge_value"))
    )

    returns_list = [
        pl.Series(
            name="do_nothing", values=do_nothing["returns"].to_numpy().flatten()[1:]
        ),
        pl.Series(name="long_put", values=long_put["returns"].to_numpy().flatten()[1:]),
        pl.Series(
            name="short_call", values=short_call["returns"].to_numpy().flatten()[1:]
        ),
        pl.Series(
            name="bear_put_spread",
            values=bear_put_spread["returns"].to_numpy().flatten()[1:],
        ),
    ]

    risk_info = risk.risk(returns=returns_list)

    var = risk_info.compute_var(99)

    all_var = pl.concat(
        [all_var, var.select("99_var").rename({"99_var": f"{hedge_date}_99_var"})],
        how="horizontal",
    )
    print("=" * 100)
    print(f"HEDGING ON {hedge_date}")

    (
        risk_info.visualize_returns(
            bins=1 / 100, title=hedge_date, n_rows=1, height=400, width=1500
        )
    )

all_var = all_var.insert_column(0, var["strategy"])

all_var

HEDGING ON 2001-09-19


Plots saved as 'histogram_plot.png' and 'distribution_plot.png'
HEDGING ON 2008-10-01


Plots saved as 'histogram_plot.png' and 'distribution_plot.png'
HEDGING ON 2010-05-11


Plots saved as 'histogram_plot.png' and 'distribution_plot.png'
HEDGING ON 2011-08-10


Plots saved as 'histogram_plot.png' and 'distribution_plot.png'
HEDGING ON 2015-08-26


Plots saved as 'histogram_plot.png' and 'distribution_plot.png'
HEDGING ON 2018-02-07


Plots saved as 'histogram_plot.png' and 'distribution_plot.png'
HEDGING ON 2020-03-02


Plots saved as 'histogram_plot.png' and 'distribution_plot.png'


shape: (4, 8)
┌────────────┬────────────┬────────────┬───────────┬───────────┬───────────┬───────────┬───────────┐
│ strategy   ┆ 2001-09-19 ┆ 2008-10-01 ┆ 2010-05-1 ┆ 2011-08-1 ┆ 2015-08-2 ┆ 2018-02-0 ┆ 2020-03-0 │
│ ---        ┆ _99_var    ┆ _99_var    ┆ 1_99_var  ┆ 0_99_var  ┆ 6_99_var  ┆ 7_99_var  ┆ 2_99_var  │
│ str        ┆ ---        ┆ ---        ┆ ---       ┆ ---       ┆ ---       ┆ ---       ┆ ---       │
│            ┆ f64        ┆ f64        ┆ f64       ┆ f64       ┆ f64       ┆ f64       ┆ f64       │
╞════════════╪════════════╪════════════╪═══════════╪═══════════╪═══════════╪═══════════╪═══════════╡
│ do_nothing ┆ -0.107875  ┆ -0.115734  ┆ -0.09593  ┆ -0.095165 ┆ -0.102319 ┆ -0.107093 ┆ -0.113423 │
│ long_put   ┆ -0.043465  ┆ -0.150068  ┆ -0.029278 ┆ -0.044589 ┆ -0.025503 ┆ -0.022824 ┆ -0.10199  │
│ short_call ┆ -0.058948  ┆ -0.081621  ┆ -0.004989 ┆ -0.067924 ┆ -0.033551 ┆ -0.026491 ┆ -0.126354 │
│ bear_put_s ┆ -0.100096  ┆ -0.259183  ┆ -0.054138 ┆ -0.068525 ┆ -0.048348 ┆ -0.046028 ┆ -0.234845 │
│ pread      ┆            ┆            ┆           ┆           ┆           ┆           ┆           │
└────────────┴────────────┴────────────┴───────────┴───────────┴───────────┴───────────┴───────────┘

# Hedging Analysis

In [11]:
ranking = (
    all_var.with_columns(
        pl.all()
        .exclude("strategy")
        .rank("ordinal", descending=True)  # rank 1 has lowest VaR
    )
    .unpivot(pl.selectors.numeric(), index="strategy")
    .rename({"value": "rank"})
    .group_by("strategy", "rank")
    .count()
    .sort(by=["rank", "count"], descending=[False, True])
)

ranking

shape: (10, 3)
┌─────────────────┬──────┬───────┐
│ strategy        ┆ rank ┆ count │
│ ---             ┆ ---  ┆ ---   │
│ str             ┆ u32  ┆ u32   │
╞═════════════════╪══════╪═══════╡
│ long_put        ┆ 1    ┆ 5     │
│ short_call      ┆ 1    ┆ 2     │
│ short_call      ┆ 2    ┆ 4     │
│ do_nothing      ┆ 2    ┆ 2     │
│ long_put        ┆ 2    ┆ 1     │
│ bear_put_spread ┆ 3    ┆ 5     │
│ short_call      ┆ 3    ┆ 1     │
│ long_put        ┆ 3    ┆ 1     │
│ do_nothing      ┆ 4    ┆ 5     │
│ bear_put_spread ┆ 4    ┆ 2     │
└─────────────────┴──────┴───────┘

In [12]:
(
    px.imshow(
        all_var.to_pandas().set_index("strategy"),
        text_auto=".1%",
        aspect="auto",
        color_continuous_scale="Reds_r",
        title="99% VaR For Each Strategy",
    )
)